In [1]:
# process_videos.py
# Usage:
# 1) put your videos into folder 'videos/' (create if needed)
# 2) run: python process_videos.py
#
# Outputs:
# - annotated videos in folder 'outputs/'
# - CSV event logs in folder 'outputs/logs/'

import os
import cv2
import math
import csv
import time
from pathlib import Path
from ultralytics import YOLO  # pip install ultralytics
import numpy as np

# ---------- CONFIG ----------
VIDEOS_DIR = "C:/Users/user/Downloads/BDDA/test/camera_videos"
OUTPUT_DIR = "C:/Users/user/Downloads/BDDA//OUTPUT_SML"
LOG_DIR = os.path.join(OUTPUT_DIR, "logs")

SAMPLE_FPS = 10
IOU_TRACKER_THRESHOLD = 0.3
SPEED_SMOOTH_FRAMES = 5


In [7]:

# GANTI YOLO12 → YOLO11
# Letakkan model YOLO kamu di folder project
MODEL_WEIGHTS = "yolo11n.pt"      # atau "best.pt" sesuai model kamu

SAMPLE_FPS = 10
IOU_TRACKER_THRESHOLD = 0.3
TAILGATE_VERTICAL_RATIO = 0.08
TAILGATE_MIN_DURATION = 3
SPEED_SMOOTH_FRAMES = 5
# -----------------------------

os.makedirs(OUTPUT_DIR, exist_ok=True)
os.makedirs(LOG_DIR, exist_ok=True)

In [8]:

# ============================
# TRACKER
# ============================
class SimpleTracker:
    def __init__(self, iou_threshold=0.3):
        self.tracks = {}
        self.next_id = 1
        self.iou_th = iou_threshold
        self.history = {}
        self.event_counters = {}

    def update(self, detections):
        assigned = set()
        new_tracks = {}

        for d in detections:
            best_id = None
            best_iou = 0.0
            for tid, bbox in self.tracks.items():
                iou = compute_iou(d, bbox)
                if iou > best_iou and iou >= self.iou_th:
                    best_iou = iou
                    best_id = tid
            if best_id is not None and best_id not in assigned:
                new_tracks[best_id] = d
                assigned.add(best_id)
            else:
                new_tracks[self.next_id] = d
                self.next_id += 1

        # update history
        for tid, bbox in new_tracks.items():
            c = bbox_center(bbox)
            if tid not in self.history:
                self.history[tid] = []
            self.history[tid].append((c, time.time()))
            if len(self.history[tid]) > 30:
                self.history[tid] = self.history[tid][-30:]

            if tid not in self.event_counters:
                self.event_counters[tid] = {'tail': 0}

        self.tracks = new_tracks
        return self.tracks

In [9]:

def compute_iou(a, b):
    ax1, ay1, ax2, ay2 = a
    bx1, by1, bx2, by2 = b
    ix1 = max(ax1, bx1); iy1 = max(ay1, by1)
    ix2 = min(ax2, bx2); iy2 = min(ay2, by2)
    iw = max(0, ix2 - ix1); ih = max(0, iy2 - iy1)
    inter = iw * ih
    area_a = max(0, (ax2 - ax1)) * max(0, (ay2 - ay1))
    area_b = max(0, (bx2 - bx1)) * max(0, (by2 - by1))
    union = area_a + area_b - inter + 1e-6
    return inter / union if union > 0 else 0.0

def bbox_center(b):
    x1,y1,x2,y2 = b
    return ((x1+x2)/2.0, (y1+y2)/2.0)

def pixel_distance(a,b):
    return math.hypot(a[0]-b[0], a[1]-b[1])

def estimate_speed(history):
    if len(history) < 2:
        return 0.0
    (c1, t1) = history[-2]
    (c2, t2) = history[-1]
    dt = t2 - t1
    if dt <= 0:
        return 0.0
    dist = pixel_distance(c1, c2)
    return dist / dt


In [10]:
# ============================
# BEHAVIOR DETECTORS
# ============================
def detect_tailgating(tracks, tracker, frame_h,
                      min_speed=30, max_gap_ratio=0.08, stable_frames=5):

    
    events = []
    
    items = list(tracks.items())  # id -> bbox

    for i in range(len(items)):
        id1, b1 = items[i]
        c1 = bbox_center(b1)

        # ---------------------------
        # CEK SPEED KENDARAAN 1
        # ---------------------------
        hist1 = tracker.history.get(id1, [])
        spd1 = estimate_speed(hist1[-SPEED_SMOOTH_FRAMES:]) if len(hist1) > 1 else 0
        if spd1 < min_speed:
            continue  # kendaraan tidak bergerak → bukan tailgating

        for j in range(len(items)):
            if i == j: continue
            
            id2, b2 = items[j]
            c2 = bbox_center(b2)

            # hanya cek kendaraan yang berada di depan
            if c2[1] < c1[1]:
                gap = c1[1] - c2[1]

                # threshold jarak y
                if gap < frame_h * max_gap_ratio:

                    # --------------------------
                    # Perlu KEDEKATAN STABIL
                    # --------------------------
                    tracker.event_counters.setdefault(id1, {'tail': 0})
                    tracker.event_counters[id1]['tail'] += 1

                    if tracker.event_counters[id1]['tail'] >= stable_frames:
                        events.append((id1, id2, gap))
                else:
                    # reset jika jarak tidak lagi dekat
                    tracker.event_counters.setdefault(id1, {'tail': 0})
                    tracker.event_counters[id1]['tail'] = 0

    return events


In [11]:
# ============================
# SPEED EVENT DETECTOR
# ============================
def detect_speed_events(
    tracker,
    speed_threshold=80,        # pixel per second (atur sesuai video)
    min_history=5,
    cooldown_frames=10
):
    """
    Mengembalikan list:
    [(track_id, speed_px_per_sec), ...]
    """

    events = []

    for tid, hist in tracker.history.items():
        if len(hist) < min_history:
            continue

        # hitung speed terbaru
        spd = estimate_speed(hist[-2:])  # px/s

        # inisialisasi counter
        tracker.event_counters.setdefault(tid, {})
        tracker.event_counters[tid].setdefault('speed_cd', 0)

        # cooldown agar tidak spam event
        if tracker.event_counters[tid]['speed_cd'] > 0:
            tracker.event_counters[tid]['speed_cd'] -= 1
            continue

        if spd >= speed_threshold:
            events.append((tid, spd))
            tracker.event_counters[tid]['speed_cd'] = cooldown_frames

    return events


In [12]:
# ============================
# MAIN VIDEO PROCESSING
# ============================
def process_video(video_path):
    vid_name = Path(video_path).stem
    cap = cv2.VideoCapture(video_path)
    if not cap.isOpened():
        print("[ERROR] cannot open", video_path)
        return

    orig_fps = cap.get(cv2.CAP_PROP_FPS) or 30.0
    width = int(cap.get(cv2.CAP_PROP_FRAME_WIDTH))
    height = int(cap.get(cv2.CAP_PROP_FRAME_HEIGHT))
    total_frames = int(cap.get(cv2.CAP_PROP_FRAME_COUNT) or 0)
    sample_step = max(1, int(round(orig_fps / SAMPLE_FPS)))

    print(f"[INFO] {vid_name}: fps={orig_fps:.1f}, size={width}x{height}, frames={total_frames}, sample_step={sample_step}")

    out_video_path = os.path.join(OUTPUT_DIR, f"{vid_name}_annotated.mp4")
    out_csv_path = os.path.join(LOG_DIR, f"{vid_name}_events.csv")

    fourcc = cv2.VideoWriter_fourcc(*'mp4v')
    out_writer = cv2.VideoWriter(out_video_path, fourcc, SAMPLE_FPS, (width, height))

        # ======================
    # LOAD YOLO11 MODEL
    # ======================
    model = YOLO(MODEL_WEIGHTS)
    tracker = SimpleTracker(iou_threshold=IOU_TRACKER_THRESHOLD)

    csvfile = open(out_csv_path, 'w', newline='')
    csvwriter = csv.writer(csvfile)
    csvwriter.writerow(['video','frame_idx','timestamp','event','subject_id','object_id','metric'])

    frame_idx = 0
    sampled_frame_idx = 0

    while True:
        ret, frame = cap.read()
        if not ret:
            break

        if frame_idx % sample_step != 0:
            frame_idx += 1
            continue

        timestamp = frame_idx / orig_fps

        # YOLO11 DETECTION
        results = model(frame)

        detections = []
        for r in results:
            if hasattr(r, 'boxes'):
                for box in r.boxes:
                    xyxy = box.xyxy.cpu().numpy().tolist()[0]
                    conf = float(box.conf.cpu().numpy()[0])
                    if conf < 0.25:
                        continue
                    detections.append(xyxy)

        tracks = tracker.update(detections)

        tail_events = detect_tailgating(tracks, frame_h=height, tracker=tracker)
        for follower, leader, gap in tail_events:
            csvwriter.writerow([vid_name, sampled_frame_idx, f"{timestamp:.2f}", "tailgating", follower, leader, f"{int(gap)}"])

        speed_evs = detect_speed_events(tracker)
        for tid, spd in speed_evs:
            csvwriter.writerow([vid_name, sampled_frame_idx, f"{timestamp:.2f}", "speed_event", tid, '', f"{spd:.2f}"])

        vis = frame.copy()
        for tid, bbox in tracks.items():
            x1,y1,x2,y2 = map(int, bbox)
            cv2.rectangle(vis, (x1,y1), (x2,y2), (0,255,0), 2)
            cv2.putText(vis, f"ID:{tid}", (x1, max(y1-6,0)), cv2.FONT_HERSHEY_SIMPLEX, 0.5, (255,255,0), 1)

        y_text = 20
        for e in tail_events:
            t_follow, t_lead, gap = e
            cv2.putText(vis, f"TAILGATE: {t_follow}->{t_lead} gap={int(gap)}", (10, y_text), cv2.FONT_HERSHEY_SIMPLEX, 0.7, (0,0,255), 2)
            y_text += 26

        for tid, spd in speed_evs:
            cv2.putText(vis, f"SPEED_EVT ID:{tid} spd={int(spd)} px/s", (10, y_text), cv2.FONT_HERSHEY_SIMPLEX, 0.7, (0,0,255), 2)
            y_text += 26

        out_writer.write(vis)

        sampled_frame_idx += 1
        frame_idx += 1

    cap.release()
    out_writer.release()
    csvfile.close()
    print(f"[DONE] processed {video_path} -> {out_video_path}, log: {out_csv_path}")

    

In [13]:
MODEL_WEIGHTS = "yolov8n.pt"
# ============================
# PROCESS ALL VIDEOS
# ============================
os.makedirs(VIDEOS_DIR, exist_ok=True)
def main():
    videos = sorted([os.path.join(VIDEOS_DIR, f) for f in os.listdir(VIDEOS_DIR)
                     if f.lower().endswith(('.mp4', '.mov', '.avi', '.mkv'))])
    if not videos:
        print("[WARN] no videos found in", VIDEOS_DIR)
        return
    for v in videos:
        process_video(v)
if __name__ == "__main__":
    main()


[INFO] 1: fps=30.0, size=1280x720, frames=300, sample_step=3

0: 384x640 4 persons, 6 cars, 1 bus, 1 truck, 134.7ms
Speed: 100.2ms preprocess, 134.7ms inference, 2.3ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 3 persons, 7 cars, 1 bus, 1 truck, 69.8ms
Speed: 2.6ms preprocess, 69.8ms inference, 3.1ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 5 persons, 6 cars, 1 truck, 64.6ms
Speed: 2.4ms preprocess, 64.6ms inference, 1.1ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 3 persons, 4 cars, 1 bus, 1 truck, 69.3ms
Speed: 2.8ms preprocess, 69.3ms inference, 1.7ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 4 persons, 6 cars, 1 truck, 69.3ms
Speed: 2.5ms preprocess, 69.3ms inference, 1.8ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 3 persons, 6 cars, 1 truck, 67.2ms
Speed: 2.5ms preprocess, 67.2ms inference, 1.2ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 6 persons, 6 cars, 1 truck, 63.6ms
Spe

In [28]:
ls -lh yolo11n.pt


-rw-r--r--@ 1 diptamulyapratama  staff   3.8M Dec 16 20:22 yolo11n.pt
